In [1]:
from language_models.elmolm_from_config import ELMOLM
from dp_components.levenshtein_searcher import LevenshteinSearcherComponent
from copy import copy, deepcopy
DATA_PATH = "/home/alx/Cloud/spell_corr/py_spelling_corrector/data/"

[nltk_data] Downloading package punkt to /home/alx/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/alx/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package perluniprops to /home/alx/nltk_data...
[nltk_data]   Package perluniprops is already up-to-date!
[nltk_data] Downloading package nonbreaking_prefixes to
[nltk_data]     /home/alx/nltk_data...
[nltk_data]   Package nonbreaking_prefixes is already up-to-date!
/home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type i

In [2]:
keke_config = {
  "chainer": {
    "in": [
      "sentences"
    ],
    "pipe": [
      {
        "in": ["sentences"],
        "class_name": "lazy_tokenizer",
        "out": ["tokens"]
      },
      {
        "class_name": "elmo_bilm",
        "mini_batch_size": 32,
        "in": [
          "tokens"
        ],
        "model_dir": "bidirectional_lms/elmo_ru_news",
        "out": [
          "pred_tokens"
        ]
      }
    ],
    "out": [
      "pred_tokens"
    ]
  },
  "metadata": {
    "requirements": [
      "../dp_requirements/tf.txt",
      "../dp_requirements/elmo.txt"
    ],
    "download": [
      {
        "url": "http://files.deeppavlov.ai/deeppavlov_data/lm_elmo_ru_news.tar.gz",
        "subdir": "bidirectional_lms/"
      }
    ]
  }
}

In [3]:
elmo = ELMOLM(keke_config)



Using TensorFlow backend.
2019-09-09 15:12:34.151 WARNING in 'tensorflow'['deprecation_wrapper'] at line 119: From /home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/deeppavlov-0.1.6-py3.6.egg/deeppavlov/models/bidirectional_lms/elmo/utils.py:40: The name tf.ConfigProto is deprecated. Please use tf.compat.v1.ConfigProto instead.

2019-09-09 15:12:34.152 WARNING in 'tensorflow'['deprecation_wrapper'] at line 119: From /home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/deeppavlov-0.1.6-py3.6.egg/deeppavlov/models/bidirectional_lms/elmo/utils.py:41: The name tf.Session is deprecated. Please use tf.compat.v1.Session instead.

2019-09-09 15:12:34.179 WARNING in 'tensorflow'['deprecation_wrapper'] at line 119: From /home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/deeppavlov-0.1.6-py3.6.egg/deeppavlov/models/bidirectional_lms/elmo/utils.py:43: The name tf.variable_scope is deprecated. Please use tf.compat.v1.variable_scope instead.

2019-09-09 15:12:34.179 WARNING in 'tensorflow

USING SKIP CONNECTIONS


2019-09-09 15:12:35.158 WARNING in 'tensorflow'['deprecation_wrapper'] at line 119: From /home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/deeppavlov-0.1.6-py3.6.egg/deeppavlov/models/bidirectional_lms/elmo/utils.py:52: The name tf.train.Saver is deprecated. Please use tf.compat.v1.train.Saver instead.

2019-09-09 15:12:35.183 WARNING in 'tensorflow'['deprecation'] at line 323: From /home/alx/Cloud/dns/.venv3/lib/python3.6/site-packages/tensorflow/python/training/saver.py:1276: checkpoint_exists (from tensorflow.python.training.checkpoint_management) is deprecated and will be removed in a future version.
Instructions for updating:
Use standard file APIs to check for files with this prefix.
2019-09-09 15:12:35.184 INFO in 'tensorflow'['saver'] at line 1280: Restoring parameters from /home/alx/Cloud/spell_corr/py_spelling_corrector/bidirectional_lms/elmo_ru_news/model.ckpt-1327437


In [4]:
# Levenshtein Hypothesis Generator
# hypotheses generator
path_to_dictionary = DATA_PATH + "compreno_wordforms.txt"
#             path_to_dictionary = DATA_PATH + "russian_words_vocab.dict"

with open(path_to_dictionary, "r") as dict_file:
    words_dict = dict_file.read().splitlines()
lsc = LevenshteinSearcherComponent(words=words_dict)

In [5]:
import numpy as np

In [19]:
sentence = "мама мыла ламу"
tok_wrapped = elmo.tokenize_sentence(sentence)

In [24]:
data = elmo.analyze_sentence(sentence)

In [26]:
probas = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped])
np.log2(probas)

array([[[-22.15323783, -13.9367338 , -21.86329607],
        [ -9.10235282, -19.28730613, -32.15470981]]])

In [40]:
sentence2 = "мама мыла раму"
tok_wrapped2 = elmo.tokenize_sentence(sentence2)
probas2 = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped2])
log_probas2 = np.log2(probas2)
log_probas2

array([[[-22.15323783, -13.9367338 , -11.24048633],
        [ -9.10235282, -19.28730613, -35.74552595]]])

In [42]:
log_probas2.sum(axis=1)

array([[-31.25559065, -33.22403993, -46.98601228]])

In [16]:
np.log2(probas)

array([[[-22.14611206, -13.94516436, -11.23673494],
        [ -8.87161181, -13.28121934, -34.07498078]]])

In [33]:
candidates_lists = lsc([tok_wrapped])
candidates_lists

[[[(0, '<S>')],
  [(-0.0, 'мама'),
   (-4.0, 'мам'),
   (-4.0, 'мамб'),
   (-4.0, 'маме'),
   (-4.0, 'мами'),
   (-4.0, 'мамо'),
   (-4.0, 'маму'),
   (-4.0, 'мамы'),
   (-4.0, 'мамае'),
   (-4.0, 'мамаи'),
   (-4.0, 'мамай'),
   (-4.0, 'мамам'),
   (-4.0, 'мамах'),
   (-4.0, 'мамаш'),
   (-4.0, 'мамаю'),
   (-4.0, 'мамая'),
   (-4.0, 'маа'),
   (-4.0, 'мага'),
   (-4.0, 'мажа'),
   (-4.0, 'маза'),
   (-4.0, 'мака'),
   (-4.0, 'мала'),
   (-4.0, 'мана'),
   (-4.0, 'мара'),
   (-4.0, 'маса'),
   (-4.0, 'мата'),
   (-4.0, 'маха'),
   (-4.0, 'маца'),
   (-4.0, 'маша'),
   (-4.0, 'ма а'),
   (-4.0, 'мамба'),
   (-4.0, 'мамка'),
   (-4.0, 'мам а'),
   (-4.0, 'мема'),
   (-4.0, 'мима'),
   (-4.0, 'м ма'),
   (-4.0, 'магма'),
   (-4.0, 'маема'),
   (-4.0, 'майма'),
   (-4.0, 'малма'),
   (-4.0, 'ма ма'),
   (-4.0, 'ама'),
   (-4.0, 'бама'),
   (-4.0, 'гама'),
   (-4.0, 'дама'),
   (-4.0, 'зама'),
   (-4.0, 'кама'),
   (-4.0, 'лама'),
   (-4.0, 'пама'),
   (-4.0, 'рама'),
   (-4.0, 'сама'),
  

In [36]:
len(candidates_lists[0])

5

In [39]:
tok_wrapped

['<S>', 'мама', 'мыла', 'ламу', '</S>']

In [ ]:
##################################################

In [89]:
sentence = "дама рыла ламу"
sentence = "на реконструкции дворца понятно что обозлились слишком хороше для киева сделал"
sentence = "ты сам себе создаешь проблемы пойми что мир не будет приклонятся перед тобой и притиратся к твоим взглядам"
tok_wrapped = elmo.tokenize_sentence(sentence)

In [90]:
data = elmo.analyze_sentence(sentence)

In [77]:
tok_wrapped

['<S>', 'дама', 'рыла', 'ламу', '</S>']

In [91]:
candidates_lists = lsc([tok_wrapped])
# find the best substitutions in sentence from candidates sets
candidates_list_for_sentence =  candidates_lists[0]
base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped])
log_probas_base = np.log(base_scores)
# summated_probas_base = log_probas_base.sum(axis=1)
summated_probas_base = log_probas_base.sum()
        
for tok_idx, each_candidates_column in enumerate(candidates_list_for_sentence[1:len(candidates_list_for_sentence)-1]):
    # find the candidate with max likelihood increment
    # find index of each candidate in row, then compare it with basis component
    print(tok_idx)
#     print(each_candidates_column)
    
    max_candidate = None
    max_candidate_score = -np.inf
    max_candidate_sentence = None
    for each_candidate_score, candidate_string in each_candidates_column:
        # sent_with_substitution
        tok_wrapped_sub = deepcopy(tok_wrapped)
        tok_wrapped_sub[tok_idx+1] = candidate_string
        probas = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped_sub])
        log_probas = np.log(probas)
#         summated_probas = log_probas.sum(axis=1)
        summated_probas = log_probas.sum()
        if summated_probas>summated_probas_base and summated_probas>max_candidate_score:
            max_candidate_score=summated_probas
            max_candidate=candidate_string
            max_candidate_sentence=tok_wrapped_sub
    print("The best substitution candidate for word_index=%d is %s. \nIt gives score increment = %f" % (tok_idx, max_candidate, max_candidate_score-summated_probas_base))
    print(max_candidate_sentence)
    
        

0
The best substitution candidate for word_index=0 is None. 
It gives score increment = -inf
None
1
The best substitution candidate for word_index=1 is None. 
It gives score increment = -inf
None
2
The best substitution candidate for word_index=2 is None. 
It gives score increment = -inf
None
3
The best substitution candidate for word_index=3 is None. 
It gives score increment = -inf
None
4
The best substitution candidate for word_index=4 is None. 
It gives score increment = -inf
None
5
The best substitution candidate for word_index=5 is None. 
It gives score increment = -inf
None
6
The best substitution candidate for word_index=6 is None. 
It gives score increment = -inf
None
7
The best substitution candidate for word_index=7 is None. 
It gives score increment = -inf
None
8
The best substitution candidate for word_index=8 is None. 
It gives score increment = -inf
None
9
The best substitution candidate for word_index=9 is None. 
It gives score increment = -inf
None
10
The best substitu

In [109]:
def elmo1_substitutor_spelling_corrector(sentence):
    
    tok_wrapped = elmo.tokenize_sentence(sentence)
    elmo_data = elmo.analyze_sentence(sentence)
    candidates_lists = lsc([tok_wrapped])
    # find the best substitutions in sentence from candidates sets
    candidates_list_for_sentence =  candidates_lists[0]
    base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch([elmo_data], [tok_wrapped])
    log_probas_base = np.log(base_scores)
    # summated_probas_base = log_probas_base.sum(axis=1)
    summated_probas_base = log_probas_base.sum()
    
    global_max_candidate = None
    global_max_candidate_score = summated_probas_base
    global_max_candidate_score_advantage = 0.0
    global_max_candidate_sentence = tok_wrapped
    
    for tok_idx, each_candidates_column in enumerate(candidates_list_for_sentence[1:len(candidates_list_for_sentence)-1]):
        # find the candidate with max likelihood increment
        # find index of each candidate in row, then compare it with basis component
#         print(tok_idx)
    #     print(each_candidates_column)

        max_candidate = None
        max_candidate_score = -np.inf
        max_candidate_sentence = None
        
        for each_candidate_score, candidate_string in each_candidates_column:
            # sent_with_substitution
            tok_wrapped_sub = deepcopy(tok_wrapped)
            tok_wrapped_sub[tok_idx+1] = candidate_string
            probas = elmo.trace_sentence_probas_in_elmo_datas_batch([elmo_data], [tok_wrapped_sub])
            log_probas = np.log(probas)
    #         summated_probas = log_probas.sum(axis=1)
            summated_probas = log_probas.sum()
            if summated_probas>summated_probas_base and summated_probas>max_candidate_score:
                max_candidate_score=summated_probas
                max_candidate=candidate_string
                max_candidate_sentence=tok_wrapped_sub
                
                # now compare it with the global best candidate
                if max_candidate_score>global_max_candidate_score:
                    global_max_candidate = max_candidate
                    global_max_candidate_score = max_candidate_score
                    global_max_candidate_sentence = max_candidate_sentence
                    global_max_candidate_score_advantage = global_max_candidate_score - summated_probas_base
        print("The best substitution candidate for word_index=%d is %s. \nIt gives score increment = %f" % (tok_idx, max_candidate, max_candidate_score-summated_probas_base))
#         print(max_candidate_sentence)
    return global_max_candidate_sentence, global_max_candidate_score_advantage, elmo_data

def elmo1_substitutor_spelling_corrector_dict_out(sentence):
    """
    Given a sentnence this method analyzes it and returns a dictionary with the best fix hypothesis
    
    As well it outputs all the data from ELMO model
    and gives information about best word substitutions in each sentence position
    
    Example of Output:
    {
        'hypothesis_sentence': 'обломно но не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве',
         'elmo_data': 
                 array([[[6.22127336e-05, 9.79734541e-05, 8.52900743e-03, ...,
                  2.94683886e-08, 3.77960863e-09, 2.58590322e-08],
                 [2.44202296e-04, 1.38270159e-04, 1.25858784e-01, ...,
                  1.32904754e-08, 1.24753914e-08, 1.73533010e-08]],

                ...,

                [[1.66291691e-04, 1.02767066e-04, 5.32708727e-02, ...,
                  3.60287311e-09, 2.54329571e-08, 3.41461899e-08],
                 [1.90042891e-04, 4.95446402e-05, 1.67940333e-02, ...,
                  3.76285598e-08, 2.79443757e-08, 3.33450672e-08]]]),
         'advantage_score': 14.520682373866407,
         'word_substitutions_candidates': [{'tok_idx': 0,
                                           'token_str': None,
                                           'advantage_score': -inf},
                                          {'tok_idx': 1, 'token_str': 'но', 'advantage_score': 14.520682373866407},
                                          {'tok_idx': 2, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 3, 'token_str': 'стал', 'advantage_score': 0.09287448556329991},
                                          {'tok_idx': 4, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 5, 'token_str': 'не', 'advantage_score': 4.452752571115013},
                                          {'tok_idx': 6, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 7, 'token_str': 'стать', 'advantage_score': 2.3514685380847027},
                                          {'tok_idx': 8,
                                           'token_str': 'последним',
                                           'advantage_score': 0.35139798958522306},
                                          {'tok_idx': 9, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 10, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 11, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 12, 'token_str': 'когда', 'advantage_score': 3.985708265575738},
                                          {'tok_idx': 13, 'token_str': 'бунт', 'advantage_score': 8.944570057290377},
                                          {'tok_idx': 14, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 15, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 16, 'token_str': 'женить', 'advantage_score': 5.92132725638271},
                                          {'tok_idx': 17,
                                           'token_str': 'выложить',
                                           'advantage_score': 0.8377485548598997},
                                          {'tok_idx': 18, 'token_str': None, 'advantage_score': -inf},
                                          {'tok_idx': 19, 'token_str': None, 'advantage_score': -inf}],
         'hypothesis_sentence_tokenized': ['<S>',
                                          'обломно',
                                          'но',
                                          'не',
                                          'сдал',
                                          'горбачева',
                                          'но',
                                          'хочу',
                                          'сдать',
                                          'последний',
                                          'экзам',
                                          'на',
                                          '5',
                                          'тогда',
                                          'буит',
                                          'возможно',
                                          'хоть',
                                          'ченить',
                                          'выловить',
                                          'на',
                                          'горбачеве',
                                          '</S>']}
    
    """
    
    tok_wrapped = elmo.tokenize_sentence(sentence)
    elmo_data = elmo.analyze_sentence(sentence)
    candidates_lists = lsc([tok_wrapped])
    # find the best substitutions in sentence from candidates sets
    candidates_list_for_sentence =  candidates_lists[0]
    base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch([elmo_data], [tok_wrapped])
    log_probas_base = np.log(base_scores)
    # summated_probas_base = log_probas_base.sum(axis=1)
    summated_probas_base = log_probas_base.sum()
    
    global_max_candidate = None
    global_max_candidate_score = summated_probas_base
    global_max_candidate_score_advantage = 0.0
    global_max_candidate_sentence = tok_wrapped
    output_dict = {
        'hypothesis_sentence': None,
        'elmo_data': elmo_data,
        'advantage_score': None,
        'word_substitutions_candidates': []
    }
    # ^^^ word substitution candidates is a list of dictionaries, where each candidate dict contains keys: 
    #         token_position: int, 
    #         candidate_word: str, 
    #         advantage_score: float 
    
    # iterate over list of levenshtein candidates lists
    for tok_idx, each_candidates_column in enumerate(candidates_list_for_sentence[1:len(candidates_list_for_sentence)-1]):
        # find the candidate with max likelihood increment
        # find index of each candidate in row, then compare it with basis component
#         print(tok_idx)
    #     print(each_candidates_column)

        max_candidate = None
        max_candidate_score = -np.inf
        max_candidate_sentence = None
        
        # iterate each levenshtein candidate in particular sentence token
        for each_candidate_score, candidate_string in each_candidates_column:
            # sent_with_substitution
            tok_wrapped_sub = deepcopy(tok_wrapped)
            tok_wrapped_sub[tok_idx+1] = candidate_string
            probas = elmo.trace_sentence_probas_in_elmo_datas_batch([elmo_data], [tok_wrapped_sub])
            log_probas = np.log(probas)
            # summated_probas = log_probas.sum(axis=1)
            summated_probas = log_probas.sum()
            if summated_probas>summated_probas_base and summated_probas>max_candidate_score:
                max_candidate_score=summated_probas
                max_candidate=candidate_string
                max_candidate_sentence=tok_wrapped_sub
                
                # now compare it with the global best candidate
                if max_candidate_score>global_max_candidate_score:
                    global_max_candidate = max_candidate
                    global_max_candidate_score = max_candidate_score
                    global_max_candidate_sentence = max_candidate_sentence
                    global_max_candidate_score_advantage = global_max_candidate_score - summated_probas_base
        # print("The best substitution candidate for word_index=%d is %s. \nIt gives score increment = %f" % (tok_idx, max_candidate, max_candidate_score-summated_probas_base))
        output_dict['word_substitutions_candidates'].append({
            'tok_idx': tok_idx,
            'token_str': max_candidate,
            'advantage_score': max_candidate_score-summated_probas_base
        })
#         print(max_candidate_sentence)
    output_dict['hypothesis_sentence_tokenized'] = global_max_candidate_sentence
    output_dict['hypothesis_sentence'] = " ".join(global_max_candidate_sentence[1:len(global_max_candidate_sentence)-1])
    output_dict['advantage_score'] = global_max_candidate_score_advantage
    
    return output_dict


####################################################################################
def elmo_analysis_with_probable_candidates_reduction_dict_out(sentence):
    """
    Given a sentnence this method analyzes it and returns a dictionary with hypotheses of the best substitutions
    this data structure allows to make parametrized hypothesis selection at the next stage.
        
    As well it outputs all the data from ELMO model
    and gives information about best word substitutions in each sentence position
    
    Example of Output:
    {
        "input_sentence": "...",
        "tokenized_input_sentence": ['<S>',
                                          'обломно',
                                          'но',
                                          'не',
                                          'сдал',
                                          'горбачева',
                                          'но',
                                          'хочу',
                                          'сдать',
                                          'последний',
                                          'экзам',
                                          'на',
                                          '5',
                                          'тогда',
                                          'буит',
                                          'возможно',
                                          'хоть',
                                          'ченить',
                                          'выловить',
                                          'на',
                                          'горбачеве',
                                          '</S>']
        "word_substitutions_candidates": [
            {'tok_idx': 0,
            'top_k_candidates': [
                    {'token_str': обломно,
                    'advantage_score': -200.0
                    },
                    {'token_str': лапа,
                    'advantage_score': -210.0
                    }
                    
                ]
            },
            {'tok_idx': 2,
            'top_k_candidates': [
                    {'token_str': но,
                    'advantage_score': -200.0
                    },
                    {'token_str': калал,
                    'advantage_score': -210.0
                    }
                    
                ]
            }
        
        ]        
    
    """
    result_data_dict = {
        'input_sentence': sentence
    }
    tok_wrapped = elmo.tokenize_sentence(sentence)
#     toks_unwrapped = tok_wrapped[1:-1]
    result_data_dict['tokenized_input_sentence'] = tok_wrapped
    
    elmo_data = elmo.analyze_sentence(sentence)
    candidates_lists = lsc([tok_wrapped])
    # find the best substitutions in sentence from candidates sets
    candidates_list_for_sentence =  candidates_lists[0]
    base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch([elmo_data], [tok_wrapped])
    log_probas_base = np.log(base_scores)
    # summated_probas_base = log_probas_base.sum(axis=1)
    summated_probas_base = log_probas_base.sum()
    
    
    # for each candidate_list by levenshtein find top_k hypothese of susbstitutions in ELMO data
    word_substitutions_candidates = [{'tok_idx': idx, 'top_k_candidates': []} for idx, _ in enumerate(candidates_list_for_sentence)]
    
#     for candi_idx, each_candidates_list in enumerate(candidates_list_for_sentence):
#         # find scores in elmo data
#         pass
    
    for tok_idx, input_token in enumerate(tok_wrapped):
        if tok_idx==0:
            continue
        
        # retieve the best candidates
        # 1. retrive best from levenshtein list
        levenshtein_candidates_for_current_token = candidates_list_for_sentence[tok_idx]
        base_left_logit, base_right_logit = elmo.retrieve_logits_of_particular_token(elmo_data, tok_idx, tok_wrapped[tok_idx])
        base_summa = base_left_logit + base_right_logit
        # 2. retrieve absolute best for the position
        for each_candidate in levenshtein_candidates_for_current_token:
            # retrieve advantage
#             print(each_candidate)
            candidate_str = each_candidate[1]
            error_score =  each_candidate[0]
            left_logit, right_logit = elmo.retrieve_logits_of_particular_token(elmo_data, tok_idx, candidate_str)
            # todo add error score?
            advantage_score = -base_summa +  left_logit  + right_logit 
            
            if advantage_score>=0:
                word_substitutions_candidates[tok_idx]['top_k_candidates'].append({
                    "advantage": advantage_score,
                    "token_str": candidate_str
                })
    
    result_data_dict['word_substitutions_candidates'] =word_substitutions_candidates
    return result_data_dict

        
from copy import deepcopy        
def fixes_maker(analysis_data, max_num_fixes=3, fix_treshold=4.5, remove_s=True):
    """
    Function which actually makes spelling correction based on analysis of sentence with data about candidates
    
    outputs corrected sentence as string
    
    :param remove_s: if true then output string contains no <s> and </s> markers in output
    """
    corrections_counter = 0
    
    
    tokens = deepcopy(analysis_data['tokenized_input_sentence'])
    
    best_substitutions_list = [{'tok_idx': tok_idx, 'best_candidate': each_tok, 'advantage': 0.0} for tok_idx, each_tok in enumerate(tokens)]
    
    # for all correction candidates find top-k fixes
    for tok_idx, each_candidates_list in enumerate(analysis_data['word_substitutions_candidates']):
        if len(each_candidates_list['top_k_candidates'])>0:
            sorted_candidates_list = sorted(each_candidates_list['top_k_candidates'], key=lambda x: x['advantage'], reverse=True)
            best_candidate_dict = sorted_candidates_list[0]
            
            # filter by treshold
            if best_candidate_dict['advantage']>fix_treshold:
                
                best_substitutions_list[tok_idx]['best_candidate']=best_candidate_dict['token_str']
                best_substitutions_list[tok_idx]['advantage']=best_candidate_dict['advantage']
    
    # now we have advantages
    # we should select top-k
    sorted_best_substitutions = sorted(best_substitutions_list, key=lambda x: x['advantage'], reverse=True)
    top_k_substitutions = sorted_best_substitutions[:max_num_fixes+1]
    
    for each_substitution_element in top_k_substitutions:
        tokens[each_substitution_element['tok_idx']] = each_substitution_element['best_candidate']
    
    if remove_s:
        output_str = " ".join(tokens[1:-1])
    else:
        output_str = " ".join(tokens)
    return output_str
        
####################################################################################
def answer_analysis_fn(input_sentence, hypo_sentence, golden_sentence, elmo_analysis_data_dict):
    """
    Method for printing results of analysis
    """
    # assert toks(input_sentence) == toks(golden_sentence)
    # find erroneous tokens.
    input_sents_toks = elmo.tokenize_sentence(input_sentence)
    hypo_sents_toks = elmo.tokenize_sentence(hypo_sentence)
    golden_sents_toks = elmo.tokenize_sentence(golden_sentence)
    
    for tok_idx, each_tok in enumerate(input_sents_toks):
        if each_tok != golden_sents_toks[tok_idx]:
            print("Tokens differ in (input) %s -> %s (golden) " % (each_tok, golden_sents_toks[tok_idx]))
            print("Hypothesis (ELMO SC with 1 substitution in sentence): %s" % hypo_sents_toks[tok_idx])
            # different tokens
            # find the elmo's hypothesis about this token            
            # get its advantage score
            # here we reduce tok_idx with 1 because word_substitutions_candidates dont list <s></s> tokens:
#             elmo_word_substitution_advantage = elmo_analysis_data_dict['word_substitutions_candidates'][tok_idx-1]['advantage_score']
            elmo_word_substitution_token = elmo_analysis_data_dict['word_substitutions_candidates'][tok_idx-1]['token_str']
            elmo_word_substitution_advantage = elmo_analysis_data_dict['word_substitutions_candidates'][tok_idx-1]['advantage_score']
            print("elmo_word_substitution_advantage for substitution: %s->%s" % (each_tok, elmo_word_substitution_token))
            print(elmo_word_substitution_advantage)
            # retrieve advantage score for golden hypothesis
            g_probas = elmo.trace_sentence_probas_in_elmo_data(elmo_data=elmo_analysis_data_dict['elmo_data'], 
                                                               tokenized_sentence=golden_sents_toks)
            log_g_probas = np.log(g_probas)
#             print(log_g_probas)
#             print(log_probas.shape)
            
            i_probas = elmo.trace_sentence_probas_in_elmo_data(elmo_data=elmo_analysis_data_dict['elmo_data'], 
                                                               tokenized_sentence=input_sents_toks)
            log_i_probas = np.log(i_probas)
            print("log_i_probas[:, tok_idx]")
            print(log_i_probas[:, tok_idx-1])
            
            print("log_g_probas[:, tok_idx]")
            print(log_g_probas[:, tok_idx-1])
            
            golden_word_substitution_advantage = log_g_probas[:, tok_idx-1].sum()-log_i_probas[:, tok_idx-1].sum()
            print("golden_word_substitution_advantage  %s->%s:" % (each_tok, golden_sents_toks[tok_idx]))
            print(golden_word_substitution_advantage)
            print("____")


# Batchy methods
def elmo1_substitutor_spelling_corrector_batch(sentences):
        
    tok_sents_wrapped = elmo.tokenize_sentence_batch(sentences)
    init_states_bak = elmo.elmo_lm.pipe[-1][-1].init_states
    elmo_datas = elmo.elmo_lm(tok_sents_wrapped)
    base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch(elmo_datas, tok_sents_wrapped)

#         data = elmo.analyze_sentence(sentence)
#         base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped])



    log_probas_base = np.log(base_scores)
    summated_probas_base = log_probas_base.sum(axis=1)
#     print(summated_probas_base)
#     print(summated_probas_base.shape)
    summated_probas_base = log_probas_base.sum()
    # TODO finsh me!!!
    
#         global_max_candidate = None
#         global_max_candidate_score = summated_probas_base
#         global_max_candidate_score_advantage = 0.0
#         global_max_candidate_sentence = tok_wrapped

#         for tok_idx, each_candidates_column in enumerate(candidates_list_for_sentence[1:len(candidates_list_for_sentence)-1]):
#             # find the candidate with max likelihood increment
#             # find index of each candidate in row, then compare it with basis component
#     #         print(tok_idx)
#         #     print(each_candidates_column)

#             max_candidate = None
#             max_candidate_score = -np.inf
#             max_candidate_sentence = None

#             for each_candidate_score, candidate_string in each_candidates_column:
#                 # sent_with_substitution
#                 tok_wrapped_sub = deepcopy(tok_wrapped)
#                 tok_wrapped_sub[tok_idx+1] = candidate_string
#                 probas = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped_sub])
#                 log_probas = np.log(probas)
#         #         summated_probas = log_probas.sum(axis=1)
#                 summated_probas = log_probas.sum()
#                 if summated_probas>summated_probas_base and summated_probas>max_candidate_score:
#                     max_candidate_score=summated_probas
#                     max_candidate=candidate_string
#                     max_candidate_sentence=tok_wrapped_sub

#                     # now compare it with the global best candidate
#                     if max_candidate_score>global_max_candidate_score:
#                         global_max_candidate = max_candidate
#                         global_max_candidate_score = max_candidate_score
#                         global_max_candidate_sentence = max_candidate_sentence
#                         global_max_candidate_score_advantage = global_max_candidate_score - summated_probas_base
#     #         print("The best substitution candidate for word_index=%d is %s. \nIt gives score increment = %f" % (tok_idx, max_candidate, max_candidate_score-summated_probas_base))
#     #         print(max_candidate_sentence)
#         return global_max_candidate_sentence, global_max_candidate_score_advantage

class SorokinELMOSpellingCorrector():
    
    def __call__(self, input_sentences):
        results_strs = []
        for each_sentence in input_sentences:
            result, advantage_score = elmo1_substitutor_spelling_corrector(each_sentence)
            # clear from <s> </s>:
            tokens = result[1:len(result)-1]
            # join list of tokens as string
            hypothesis_str = " ".join(tokens)
            print("For input sentence:\n %s "%each_sentence)
            print("Hypothesis:\n %s " % hypothesis_str)
            print("Advantage score:\n %f "% advantage_score)
            results_strs.append(hypothesis_str)
        return results_strs
    
    
        
class SorokinELMOMultiSpellingCorrector():
    def __init__(self):
        pass
    
    def calculate_elmo_data(self, sentence):
        pass
    
    def probable_candidates_reduction(self, elmo_data, levenshtein_candidates_list_of_lists, **kwargs):
        """
        Given ELMO data matrix and levenshtein candidates it produces the space of candidates which consumes less memory because low probable candidates are removed
        """
        pass
    
    def parametrized_best_hypothesis_selection(self, candidates_space, max_substitution):
        """
        """
        pass
    
    # batchy methods
    def calculate_elmo_datas(self, sentences_batch):
        pass
    
selmosc = SorokinELMOSpellingCorrector()

In [ ]:
###################################################################################################

In [38]:
# multicandidates analysis
res_dict = elmo_analysis_with_probable_candidates_reduction_dict_out("мамы мыла грязную раму")
res_dict

{'input_sentence': 'мамы мыла грязную раму',
 'tokenized_input_sentence': ['<S>',
  'мамы',
  'мыла',
  'грязную',
  'раму',
  '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
  {'tok_idx': 1,
   'top_k_candidates': [{'advantage': 0.0, 'token_str': 'мамы'},
    {'advantage': 6.250780079464014, 'token_str': 'мама'}]},
  {'tok_idx': 2,
   'top_k_candidates': [{'advantage': 1.7763568394002505e-15,
     'token_str': 'мыла'},
    {'advantage': 0.9064977574460951, 'token_str': 'была'}]},
  {'tok_idx': 3,
   'top_k_candidates': [{'advantage': 1.7763568394002505e-15,
     'token_str': 'грязную'}]},
  {'tok_idx': 4,
   'top_k_candidates': [{'advantage': 3.552713678800501e-15,
     'token_str': 'раму'},
    {'advantage': 1.4746532629264664, 'token_str': 'рану'},
    {'advantage': 0.5865288537296784, 'token_str': 'маму'}]},
  {'tok_idx': 5,
   'top_k_candidates': [{'advantage': 1.7763568394002505e-15,
     'token_str': '</S>'}]}]}

In [11]:
res_dict

In [ ]:
###################################################################################################

In [24]:
input_sentence =  "давно стоит понять что в этой жизни никто не зделает так как лутче тебе"
golden_sentence = "давно стоит понять что в этой жизни никто не сделает так как лучше тебе"


input_sentence = "двубортное кашемировое пальто песочного цвета классическог фасона"
golden_sentence ="двубортное кашемировое пальто песочного цвета классического фасона"

input_sentence = "только не сделай мне уроки воть покажу те тогда кузькину мать"
golden_sentence ="только не сделай мне уроки вот покажу тебе тогда кузькину мать"

input_sentence = "фишкой нашего прибывания в нью-йорке стала вполне шикарная квартира в центре города на манхеттоне на 27 этаже с прекрасным видом"
golden_sentence ="фишкой нашего пребывания в нью-йорке стала вполне шикарная квартира в центре города на манхэттене на 27 этаже с прекрасным видом"

input_sentence = "на этой неделе я простудился и последние дни вечром не гулял"
golden_sentence ="на этой неделе я простудился и последние дни вечером не гулял"

input_sentence = "обломно шо не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве"
golden_sentence ="обломно что не сдал горбачева но хочу сдать последний экзамен на 5 тогда будет возможно хоть что-нибудь выловить на горбачеве"
res = elmo1_substitutor_spelling_corrector_dict_out(input_sentence)
res

{'hypothesis_sentence': 'обломно но не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве',
 'elmo_data': array([[[6.22127336e-05, 9.79734541e-05, 8.52900743e-03, ...,
          2.94683886e-08, 3.77960863e-09, 2.58590322e-08],
         [2.44202296e-04, 1.38270159e-04, 1.25858784e-01, ...,
          1.32904754e-08, 1.24753914e-08, 1.73533010e-08]],
 
        [[6.57977143e-05, 1.45196231e-04, 9.45733022e-03, ...,
          2.88660775e-08, 3.99531075e-09, 2.79607306e-08],
         [3.84539191e-04, 2.49398930e-04, 1.36887670e-01, ...,
          1.06430686e-08, 6.16177998e-09, 1.55451136e-08]],
 
        [[1.15585251e-04, 2.17194523e-04, 1.54366018e-02, ...,
          4.70958739e-08, 4.64493022e-09, 2.81024732e-08],
         [1.20606921e-04, 7.57123562e-05, 2.84761041e-02, ...,
          1.79602244e-09, 2.01377603e-09, 2.03773909e-09]],
 
        ...,
 
        [[1.08595501e-04, 2.57026895e-05, 7.30334297e-02, ...,
          4.62868144e-0

In [25]:
input_sentence = "обломно шо не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве"
golden_sentence ="обломно что не сдал горбачева но хочу сдать последний экзамен на 5 тогда будет возможно хоть что-нибудь выловить на горбачеве"
res = elmo1_substitutor_spelling_corrector_dict_out(input_sentence)
res
print("input_sentence:")
print(input_sentence)
print("golden_sentence:")
print(golden_sentence)
print("hypothesis_sentence:")
print(res['hypothesis_sentence'])

results = answer_analysis_fn(input_sentence, res['hypothesis_sentence'], golden_sentence, res)
results

input_sentence:
обломно шо не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве
golden_sentence:
обломно что не сдал горбачева но хочу сдать последний экзамен на 5 тогда будет возможно хоть что-нибудь выловить на горбачеве
hypothesis_sentence:
обломно но не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве
Tokens differ in (input) шо -> что (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): но
elmo_word_substitution_advantage for substitution: но
14.520682373866407
UNK: обломно
UNK: горбачева
UNK: горбачеве
UNK: обломно
UNK: горбачева
UNK: экзам
UNK: буит
UNK: ченить
UNK: горбачеве
log_i_probas[:, tok_idx]
[-14.52765854 -12.4964751 ]
log_g_probas[:, tok_idx]
[-6.98338231 -3.79996092]
golden_word_substitution_advantage
16.240790413756223
____
Tokens differ in (input) экзам -> экзамен (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): экзам
elmo_word_subst

In [ ]:
# analyze all sentences:


In [119]:
# elmo1_substitutor_spelling_corrector_batch()
sentences = ["дама рыла ламу", "на реконструкции дворца понятно что обозлились слишком хороше для киева сделал"]
tok_sents_wrapped = elmo.tokenize_sentence_batch(sentences)
init_states_bak = elmo.elmo_lm.pipe[-1][-1].init_states
elmo_datas = elmo.elmo_lm(tok_sents_wrapped)
base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch(elmo_datas, tok_sents_wrapped)
print(base_scores)

# print(base_scores.shape)
#         data = elmo.analyze_sentence(sentence)
#         base_scores = elmo.trace_sentence_probas_in_elmo_datas_batch([data], [tok_wrapped])

# iter over all sentence and calc log for each array of probas:
log_probas_base_list = [np.log(each_base_score) for each_base_score in base_scores]

# log_probas_base = np.log(base_scores)
summated_probas_base_list = [log_probas_base.sum() for log_probas_base in log_probas_base_list]
# summated_probas_base = 
print(summated_probas_base_list)
# print(summated_probas_base.shape)
# summated_probas_base = log_probas_base.sum()


[array([[7.67007933e-08, 7.33689205e-07, 3.20397788e-07],
       [7.01467288e-05, 2.22732098e-07, 6.27141325e-11]]), array([[5.72935242e-05, 6.33739692e-05, 3.11371568e-03, 4.79164612e-07,
        7.18107540e-03, 2.94534885e-08, 1.28356187e-04, 3.01843563e-08,
        2.23195199e-02, 1.56462211e-08, 2.13568364e-06],
       [1.20488945e-02, 1.36160714e-04, 2.37494987e-06, 6.59770967e-06,
        1.85499284e-02, 2.86903870e-08, 2.25196164e-02, 2.43085168e-07,
        3.70572917e-02, 3.41610750e-09, 5.41347411e-09]])]
[-93.83688845676474, -243.5438211876558]


In [120]:
tok_sents_wrapped

[['<S>', 'дама', 'рыла', 'ламу', '</S>'],
 ['<S>',
  'на',
  'реконструкции',
  'дворца',
  'понятно',
  'что',
  'обозлились',
  'слишком',
  'хороше',
  'для',
  'киева',
  'сделал',
  '</S>']]

In [118]:
base_scores[1]

array([[5.73220750e-05, 6.35112956e-05, 3.11391475e-03, 4.72404082e-07,
        7.17164250e-03, 2.92272908e-08, 1.28683518e-04, 3.07547445e-08,
        2.24800631e-02, 1.57347098e-08, 2.14406555e-06],
       [1.20427189e-02, 1.36096001e-04, 2.37777272e-06, 6.59493253e-06,
        1.85337868e-02, 2.86439903e-08, 2.25926619e-02, 2.42813456e-07,
        3.70665528e-02, 3.40782129e-09, 5.37424905e-09]])

In [99]:
selmosc(["дама рыла ламу"])

For input sentence:
дама рыла ламу 
Hypothesis:
дама была ламу 
Advantage score:
14.601998 


['дама была ламу']

In [93]:
sentence = "дама рыла ламу"
sentence = "на реконструкции дворца понятно что обозлились слишком хороше для киева сделал"
sentence = "ты сам себе создаешь проблемы пойми что мир не будет приклонятся перед тобой и притиратся к твоим взглядам"
elmo1_substitutor_spelling_corrector(sentence)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17


(['<S>',
  'ты',
  'сам',
  'себе',
  'создаешь',
  'проблемы',
  'пойми',
  'что',
  'мир',
  'не',
  'будет',
  'приклонятся',
  'перед',
  'тобой',
  'и',
  'притирается',
  'к',
  'твоим',
  'взглядам',
  '</S>'],
 11.892095549849955)

In [84]:
max_candidate_sentence

['<S>', 'дама', 'рыла', 'лапу', '</S>']

# Evaluate model

In [39]:
DIALOG_DATA_PATH = 'data/dialog/'
# Train data
TRAIN_ERRONEOUS_DATA = DIALOG_DATA_PATH + "source_sents.txt"
TRAIN_GOLDEN_DATA = DIALOG_DATA_PATH + "corrected_sents.txt"

# Test data
TEST_ERRONEOUS_DATA = DIALOG_DATA_PATH + "test_sample_testset.txt"
TEST_GOLDEN_DATA = DIALOG_DATA_PATH + "corr_sample_testset.txt"

In [144]:
# with open(TEST_ERRONEOUS_DATA, 'r') as sents_file:
with open(TRAIN_ERRONEOUS_DATA, 'r') as sents_file:
    erroneous_lines = sents_file.readlines()
    erroneous_lines = [line.strip() for line in erroneous_lines]
    
# with open(TEST_GOLDEN_DATA, 'r') as sents_file:
with open(TRAIN_GOLDEN_DATA, 'r') as sents_file:
    golden_lines = sents_file.readlines()
    golden_lines = [line.strip() for line in golden_lines]

In [41]:
from evaluate import evaluate_spelling_corrector
import datetime as dt

In [ ]:
################################################################################

In [103]:
# loop over sentences that has the same number of tokens as in correct answer
hypotheses = []
filtered_erroneous_lines = []
filtered_golden_lines = []
start_dt = dt.datetime.now()
for idx, each_error_line in enumerate(erroneous_lines):
    err_toks = each_error_line.split()
    gold_toks = golden_lines[idx].split()
    if len(gold_toks) == len(err_toks):
        
        print("Sentence with the same number of toks:\n %s" % each_error_line)
        print("Golden answer:\n %s" % golden_lines[idx])
        
        result = selmosc([each_error_line])[0]
        
        filtered_erroneous_lines.append(each_error_line)
        filtered_golden_lines.append(golden_lines[idx])
        hypotheses.append(result)
        
        print("Hypothesis answer:\n %s" % result)
        print("___")
fin_dt = dt.datetime.now()
print("Total time for inference:")
print(fin_dt-start_dt)
results = evaluate_spelling_corrector(filtered_erroneous_lines, 
                                      filtered_golden_lines, 
                                      hypotheses)
print(results['precision'])
print(results['recall'])
print(results['f_measure'])

Sentence with the same number of toks:
 ﻿есть у вас оформленый и подписаный мною заказ
Golden answer:
 ﻿есть у вас оформленный и подписанный мною заказ
For input sentence:
 ﻿есть у вас оформленый и подписаный мною заказ 
Hypothesis:
 ﻿есть у вас оформленый и подписанный мною заказ 
Advantage score:
 22.154368 
Hypothesis answer:
 ﻿есть у вас оформленый и подписанный мною заказ
___
Sentence with the same number of toks:
 вот в инете откапал такую интеерсную статейку предлагаю вашему внимани
Golden answer:
 вот в инете откопал такую интересную статейку предлагаю вашему вниманию
For input sentence:
 вот в инете откапал такую интеерсную статейку предлагаю вашему внимани 
Hypothesis:
 вот в инете откапал такую интеерсную статейку предлагаю вашему вниманию 
Advantage score:
 23.023388 
Hypothesis answer:
 вот в инете откапал такую интеерсную статейку предлагаю вашему вниманию
___
Sentence with the same number of toks:
 я на всю жизнь запомню свое первое купание в зимнем ледяном енисее
Golden

For input sentence:
 акцент в последнем предложении правда не совсем понятен 
Hypothesis:
 акцент в последнем предложении правда не совсем понятен 
Advantage score:
 0.000000 
Hypothesis answer:
 акцент в последнем предложении правда не совсем понятен
___
Sentence with the same number of toks:
 в детстве я был толстым кучерявым и чрезвычайно прожорливым блондином
Golden answer:
 в детстве я был толстым кучерявым и чрезвычайно прожорливым блондином
For input sentence:
 в детстве я был толстым кучерявым и чрезвычайно прожорливым блондином 
Hypothesis:
 в детстве я был толстым кучерявый и чрезвычайно прожорливым блондином 
Advantage score:
 7.968827 
Hypothesis answer:
 в детстве я был толстым кучерявый и чрезвычайно прожорливым блондином
___
Sentence with the same number of toks:
 он сейчас в отъезде но почту проверять должен переодически
Golden answer:
 он сейчас в отъезде но почту проверять должен периодически
For input sentence:
 он сейчас в отъезде но почту проверять должен переодиче

For input sentence:
 уничтоженный пожаром каменный храм восстановили своими силами в 1860 году уральские казаки 
Hypothesis:
 уничтоженный пожаром каменный храм восстановили своими силами в 1860 году уральские казаки 
Advantage score:
 0.000000 
Hypothesis answer:
 уничтоженный пожаром каменный храм восстановили своими силами в 1860 году уральские казаки
___
Sentence with the same number of toks:
 дело и в том что белоруссия единственная постсоветская республика которая смогла переломить предначертанный ей ход событий остаться независимой и идти собственным путем
Golden answer:
 дело и в том что белоруссия единственная постсоветская республика которая смогла переломить предначертанный ей ход событий остаться независимой и идти собственным путем
For input sentence:
 дело и в том что белоруссия единственная постсоветская республика которая смогла переломить предначертанный ей ход событий остаться независимой и идти собственным путем 
Hypothesis:
 дело и в том что белоруссия единственная 

For input sentence:
 не доверят то что очень хочеться попробывать и из-за этого какой-то неполноценной себя чувствовать начинаешь 
Hypothesis:
 не доверят то что очень хочется попробывать и из-за этого какой-то неполноценной себя чувствовать начинаешь 
Advantage score:
 24.094381 
Hypothesis answer:
 не доверят то что очень хочется попробывать и из-за этого какой-то неполноценной себя чувствовать начинаешь
___
Sentence with the same number of toks:
 было бы желание а уж понятия тоталитарная секта и деструктивный культ всегда готовы принять в свои безразмерные объятия всякого кого нужно ничтоже сумняшеся заклеймить не утруждая себя задуматься о последствиях бездумного обращения с такими ярлыками-страшилками
Golden answer:
 было бы желание а уж понятия тоталитарная секта и деструктивный культ всегда готовы принять в свои безразмерные объятия всякого кого нужно ничтоже сумняшеся заклеймить не утруждая себя задуматься о последствиях бездумного обращения с такими ярлыками-страшилками
For in

For input sentence:
 и песня вертинского мне кажется эти сомнения подкрепляет 
Hypothesis:
 и песня вертинского мне кажется эти сомнения подкрепляют 
Advantage score:
 1.627316 
Hypothesis answer:
 и песня вертинского мне кажется эти сомнения подкрепляют
___
Sentence with the same number of toks:
 а вот про поликлиники бесплатные очнь хорошо понимаю
Golden answer:
 а вот про поликлиники бесплатные очень хорошо понимаю
For input sentence:
 а вот про поликлиники бесплатные очнь хорошо понимаю 
Hypothesis:
 а вот про поликлиники бесплатные очень хорошо понимаю 
Advantage score:
 29.136963 
Hypothesis answer:
 а вот про поликлиники бесплатные очень хорошо понимаю
___
Sentence with the same number of toks:
 только не сделай мне уроки воть покажу те тогда кузькину мать
Golden answer:
 только не сделай мне уроки вот покажу тебе тогда кузькину мать
For input sentence:
 только не сделай мне уроки воть покажу те тогда кузькину мать 
Hypothesis:
 только не сделай мне уроки вот покажу те тогда куз

...

For input sentence:
 а в январе я размазжил бошку 
Hypothesis:
 а в январе я размазжил бочку 
Advantage score:
 11.062375 
Hypothesis answer:
 а в январе я размазжил бочку
___
Sentence with the same number of toks:
 но так как система эта все равно не работала открывали мы подъездную дверь ключом
Golden answer:
 но так как система эта все равно не работала открывали мы подъездную дверь ключом
For input sentence:
 но так как система эта все равно не работала открывали мы подъездную дверь ключом 
Hypothesis:
 но так как система эта все равно не работала открывали бы подъездную дверь ключом 
Advantage score:
 5.940139 
Hypothesis answer:
 но так как система эта все равно не работала открывали бы подъездную дверь ключом
___
Sentence with the same number of toks:
 теория вероятности это интеренсо правда интересно
Golden answer:
 теория вероятности это интересно правда интересно
For input sentence:
 теория вероятности это интеренсо правда интересно 
Hypothesis:
 теория вероятности это интере

For input sentence:
 после этого мы отправились на фестиваль музыки fado правда успели только на конец 
Hypothesis:
 после этого мы отправились на фестиваль музыки fado правда успели только на конец 
Advantage score:
 0.000000 
Hypothesis answer:
 после этого мы отправились на фестиваль музыки fado правда успели только на конец
___
Sentence with the same number of toks:
 в частности lionsgate предлагала владельцам франшизы 15 миллионов долларов наличными а также обещала пять процентов от сборов всех последующих фильмов
Golden answer:
 в частности lionsgate предлагала владельцам франшизы 15 миллионов долларов наличными а также обещала пять процентов от сборов всех последующих фильмов
For input sentence:
 в частности lionsgate предлагала владельцам франшизы 15 миллионов долларов наличными а также обещала пять процентов от сборов всех последующих фильмов 
Hypothesis:
 в частности lionsgate предлагала владельцам франшизы 15 миллионов долларов наличными и также обещала пять процентов от сбо

For input sentence:
 ну что у него были последователи относящиеся к нему как к великому магистру у которых и на деньги которых он и жил 
Hypothesis:
 на что у него были последователи относящиеся к нему как к великому магистру у которых и на деньги которых он и жил 
Advantage score:
 7.226000 
Hypothesis answer:
 на что у него были последователи относящиеся к нему как к великому магистру у которых и на деньги которых он и жил
___
Sentence with the same number of toks:
 ну так это ж абсолютно естесственно
Golden answer:
 ну так это ж абсолютно естественно
For input sentence:
 ну так это ж абсолютно естесственно 
Hypothesis:
 ну так это ж абсолютно естественно 
Advantage score:
 15.934567 
Hypothesis answer:
 ну так это ж абсолютно естественно
___
Sentence with the same number of toks:
 а кстате в четверг пересекаемся
Golden answer:
 а кстати в четверг пересекаемся
For input sentence:
 а кстате в четверг пересекаемся 
Hypothesis:
 а кстати в четверг пересекаемся 
Advantage score:
 16.3486

For input sentence:
 короче сегоднешний поход в как принято говорить бутик за зимней парой сапог закончился покупкой таковых 36 размера 
Hypothesis:
 короче сегодняшний поход в как принято говорить бутик за зимней парой сапог закончился покупкой таковых 36 размера 
Advantage score:
 17.031905 
Hypothesis answer:
 короче сегодняшний поход в как принято говорить бутик за зимней парой сапог закончился покупкой таковых 36 размера
___
Sentence with the same number of toks:
 речь обамки последняя попытка сплотить запад
Golden answer:
 речь обамки последняя попытка сплотить запад
For input sentence:
 речь обамки последняя попытка сплотить запад 
Hypothesis:
 речь обамки последняя попытка сплотить запас 
Advantage score:
 1.972675 
Hypothesis answer:
 речь обамки последняя попытка сплотить запас
___
Sentence with the same number of toks:
 срубил страшную голову луг но воздвиг ее на каменный столб
Golden answer:
 срубил страшную голову луг но воздвиг ее на каменный столб
For input sentence:
 ср

For input sentence:
 после эти сообщения опровергались затем появлялись снова 
Hypothesis:
 после эти сообщения опровергались затем появлялись снова 
Advantage score:
 0.000000 
Hypothesis answer:
 после эти сообщения опровергались затем появлялись снова
___
Sentence with the same number of toks:
 наверное в моем возрасте и с моим образованием стыдно в этом признаваца но мне чем-то нравица бен стиллер
Golden answer:
 наверное в моем возрасте и с моим образованием стыдно в этом признаваться но мне чем-то нравится бен стиллер
For input sentence:
 наверное в моем возрасте и с моим образованием стыдно в этом признаваца но мне чем-то нравица бен стиллер 
Hypothesis:
 наверное в моем возрасте и с моим образованием стыдно в этом признаваца но мне чем-то нравица без стиллер 
Advantage score:
 14.076622 
Hypothesis answer:
 наверное в моем возрасте и с моим образованием стыдно в этом признаваца но мне чем-то нравица без стиллер
___
Sentence with the same number of toks:
 человек который согласн

# 190909 Analyze advantages of LM for Golden Word and for hypothesis

for all sentences in dataset calculate data sdtructure with that analysos


In [46]:
import pprint

In [145]:
# loop over sentences that has the same number of tokens as in correct answer
hypotheses = []
filtered_erroneous_lines = []
filtered_golden_lines = []
start_dt = dt.datetime.now()
results_data = []
for idx, each_error_line in enumerate(erroneous_lines):
#     if idx<3:continue
    err_toks = each_error_line.split()
    gold_toks = golden_lines[idx].split()
    if len(gold_toks) == len(err_toks):
        
#         print("Sentence with the same number of toks:\n %s" % each_error_line)
#         print("Golden answer:\n %s" % golden_lines[idx])
#         input_sentence = "обломно шо не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве"
#         golden_sentence ="обломно что не сдал горбачева но хочу сдать последний экзамен на 5 тогда будет возможно хоть что-нибудь выловить на горбачеве"
        res = elmo_analysis_with_probable_candidates_reduction_dict_out(each_error_line)
        res['golden_sentence'] = golden_lines[idx]
        pprint.pprint(res)
        results_data.append(res)
#         res
#         print("input_sentence:")
#         print(input_sentence)
#         print("golden_sentence:")
#         print(golden_sentence)
#         print("hypothesis_sentence:\n %s" % res['hypothesis_sentence'])
#         print("Hypothesis answer:\n %s" % res['hypothesis_sentence'])

#         results = answer_analysis_fn(each_error_line, res['hypothesis_sentence'], golden_lines[idx], res)
# #         results
#         result = selmosc([each_error_line])[0]
        
#         filtered_erroneous_lines.append(each_error_line)
#         filtered_golden_lines.append(golden_lines[idx])
#         hypotheses.append(res['hypothesis_sentence'])
        
#         
        print("________________________________________")
#     if idx>13:
#         break
fin_dt = dt.datetime.now()
print("Total time for inference:")
print(fin_dt-start_dt)
# results = evaluate_spelling_corrector(filtered_erroneous_lines, 
#                                       filtered_golden_lines, 
#                                       hypotheses)
# print(results['precision'])
# print(results['recall'])
# print(results['f_measure'])

{'golden_sentence': 'Может выгоднее втулку продать и купить колесо в сборе',
 'input_sentence': 'Может выгоднее втулку продать и купить колесо в сборе?',
 'tokenized_input_sentence': ['<S>',
                              'Может',
                              'выгоднее',
                              'втулку',
                              'продать',
                              'и',
                              'купить',
                              'колесо',
                              'в',
                              'сборе?',
                              '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1, 'top_k_candidates': []},
                                   {'tok_idx': 2,
                                    'top_k_candidates': [{'advantage': 0.0,
                                                          'token_str': 'выгоднее'}]},
                                   {'tok_idx': 3,
      

{'golden_sentence': 'Хотя странно когда я забирала к себе на выходные старого '
                    'кота который живет у родителей да и собаку в придачу то '
                    'такого концерта мой кот не устраивал',
 'input_sentence': 'Хотя странно, когда я забирала к себе на выходные старого '
                   'кота, который живет у родителей, да и собаку в придачу, то '
                   'такого концерта мой кот не устраивал.',
 'tokenized_input_sentence': ['<S>',
                              'Хотя',
                              'странно,',
                              'когда',
                              'я',
                              'забирала',
                              'к',
                              'себе',
                              'на',
                              'выходные',
                              'старого',
                              'кота,',
                              'который',
                              'живет',
                

{'golden_sentence': 'Думаю что лет через 10 ретроспективно просматривать это '
                    'будет мне невероятно интересно',
 'input_sentence': 'Думаю, что лет через 10 ретроспективно просматривать это '
                   'будет мне невероятно интересно.',
 'tokenized_input_sentence': ['<S>',
                              'Думаю,',
                              'что',
                              'лет',
                              'через',
                              '10',
                              'ретроспективно',
                              'просматривать',
                              'это',
                              'будет',
                              'мне',
                              'невероятно',
                              'интересно.',
                              '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1,
                                    'top_k_candi

{'golden_sentence': 'Поясним эту мысль',
 'input_sentence': 'Пояним эту мысль.',
 'tokenized_input_sentence': ['<S>', 'Пояним', 'эту', 'мысль.', '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1, 'top_k_candidates': []},
                                   {'tok_idx': 2, 'top_k_candidates': []},
                                   {'tok_idx': 3,
                                    'top_k_candidates': [{'advantage': 16.27627135159954,
                                                          'token_str': 'мысль'},
                                                         {'advantage': 4.885301184137155,
                                                          'token_str': 'мыслью'},
                                                         {'advantage': 3.552713678800501e-15,
                                                          'token_str': 'мысль.'}]},
                                   {'tok_idx': 4,


{'golden_sentence': 'Роспись была назначена на вторую половину дня поэтому '
                    'время на прогулку и фотосессию было ограничено',
 'input_sentence': 'Роспись была назначена на вторую половину дня, поэтому '
                   'время на прогулку и фотосессию было ограничено.',
 'tokenized_input_sentence': ['<S>',
                              'Роспись',
                              'была',
                              'назначена',
                              'на',
                              'вторую',
                              'половину',
                              'дня,',
                              'поэтому',
                              'время',
                              'на',
                              'прогулку',
                              'и',
                              'фотосессию',
                              'было',
                              'ограничено.',
                              '</S>'],
 'word_substitutions_candidates'

...

{'golden_sentence': 'Спутник позволит наблюдать за потенциально опасными '
                    'явлениями в атмосфере Земли',
 'input_sentence': 'Спутник позволит наблюдать за потенциально опасными '
                   'явлениями в атмосфере Земли.',
 'tokenized_input_sentence': ['<S>',
                              'Спутник',
                              'позволит',
                              'наблюдать',
                              'за',
                              'потенциально',
                              'опасными',
                              'явлениями',
                              'в',
                              'атмосфере',
                              'Земли.',
                              '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1, 'top_k_candidates': []},
                                   {'tok_idx': 2,
                                    'top_k_candidates': [{'adv

{'golden_sentence': 'Прочитала тут новость что 21 июля то есть в день выхода '
                    'седьмой книги начнет работать телефон доверия чтобы '
                    'прочитавшие поттероманы туда звонили и их смогли убедить '
                    'что жизнь еще не кончилась',
 'input_sentence': 'Прочтала тут новость, что 21 июля, то есть в день выхода '
                   'седьмой книги начнет работать телефон доверия, чтобы '
                   'прочитавшие поттероманы туда звонили и их смогли убедить, '
                   'что жизни еще не кончилась.',
 'tokenized_input_sentence': ['<S>',
                              'Прочтала',
                              'тут',
                              'новость,',
                              'что',
                              '21',
                              'июля,',
                              'то',
                              'есть',
                              'в',
                              'день',
               

{'golden_sentence': 'Я тоже очень люблю их иначе бы задача тети провалилась',
 'input_sentence': 'Я тоже оччень люблю их, иначе бы задача тети провалилась.',
 'tokenized_input_sentence': ['<S>',
                              'Я',
                              'тоже',
                              'оччень',
                              'люблю',
                              'их,',
                              'иначе',
                              'бы',
                              'задача',
                              'тети',
                              'провалилась.',
                              '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1, 'top_k_candidates': []},
                                   {'tok_idx': 2, 'top_k_candidates': []},
                                   {'tok_idx': 3,
                                    'top_k_candidates': [{'advantage': 31.855128746536398,
            

{'golden_sentence': 'Прекратите этот дождь из событий',
 'input_sentence': 'Прератите этот дождь из событий',
 'tokenized_input_sentence': ['<S>',
                              'Прератите',
                              'этот',
                              'дождь',
                              'из',
                              'событий',
                              '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1,
                                    'top_k_candidates': [{'advantage': 0.0,
                                                          'token_str': 'Прератите'}]},
                                   {'tok_idx': 2,
                                    'top_k_candidates': [{'advantage': 8.881784197001252e-16,
                                                          'token_str': 'этот'}]},
                                   {'tok_idx': 3,
                                    'top_k_candidates

{'golden_sentence': 'Какой-то период времени мы вообще не общались',
 'input_sentence': 'Какой-то период времени мы вобще не общались...',
 'tokenized_input_sentence': ['<S>',
                              'Какой-то',
                              'период',
                              'времени',
                              'мы',
                              'вобще',
                              'не',
                              'общались...',
                              '</S>'],
 'word_substitutions_candidates': [{'tok_idx': 0, 'top_k_candidates': []},
                                   {'tok_idx': 1,
                                    'top_k_candidates': [{'advantage': 8.881784197001252e-16,
                                                          'token_str': 'Какой-то'}]},
                                   {'tok_idx': 2,
                                    'top_k_candidates': [{'advantage': 8.881784197001252e-16,
                                                         

In [108]:
idx = 41
print(fixes_maker(results_data[idx], max_num_fixes=5, fix_treshold=5, remove_s=True))
pprint.pprint(results_data[idx])

не доверят то что очень хочется попробовать и из-за этого какой-то неполноценной себя чувствовать начинаешь
{'golden_sentence': 'не доверят то что очень хочется попробовать и из-за этого '
                    'какой-то неполноценной себя чувствовать начинаешь',
 'input_sentence': 'не доверят то что очень хочеться попробывать и из-за этого '
                   'какой-то неполноценной себя чувствовать начинаешь',
 'tokenized_input_sentence': ['<S>',
                              'не',
                              'доверят',
                              'то',
                              'что',
                              'очень',
                              'хочеться',
                              'попробывать',
                              'и',
                              'из-за',
                              'этого',
                              'какой-то',
                              'неполноценной',
                              'себя',
                              'ч

In [151]:
len(results_data)

1373

In [150]:
for idx, each_dict in enumerate(results_data):
    if each_dict['golden_sentence']!=each_dict['input_sentence']:
        print(idx)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
112
113
114
115
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
28

In [121]:
np.arange(1, 6)

array([1, 2, 3, 4, 5])

In [146]:
# lets evaluate fixes model
# 1. lets produce famili of fixers
# max_num_fixes_params = (1,2,3,4,5)
# fix_treshold_params = 

from sklearn.model_selection import ParameterGrid
param_grid = {
    'max_num_fixes': np.arange(1, 6), 
    'fix_treshold': np.linspace(1.0, 20.0, 5)}
parameters_grid_list = list(ParameterGrid(param_grid))
print(list(ParameterGrid(param_grid)))

# fixes_maker(results_data[idx], max_num_fixes=5, fix_treshold=5, remove_s=True)

[{'fix_treshold': 1.0, 'max_num_fixes': 1}, {'fix_treshold': 1.0, 'max_num_fixes': 2}, {'fix_treshold': 1.0, 'max_num_fixes': 3}, {'fix_treshold': 1.0, 'max_num_fixes': 4}, {'fix_treshold': 1.0, 'max_num_fixes': 5}, {'fix_treshold': 5.75, 'max_num_fixes': 1}, {'fix_treshold': 5.75, 'max_num_fixes': 2}, {'fix_treshold': 5.75, 'max_num_fixes': 3}, {'fix_treshold': 5.75, 'max_num_fixes': 4}, {'fix_treshold': 5.75, 'max_num_fixes': 5}, {'fix_treshold': 10.5, 'max_num_fixes': 1}, {'fix_treshold': 10.5, 'max_num_fixes': 2}, {'fix_treshold': 10.5, 'max_num_fixes': 3}, {'fix_treshold': 10.5, 'max_num_fixes': 4}, {'fix_treshold': 10.5, 'max_num_fixes': 5}, {'fix_treshold': 15.25, 'max_num_fixes': 1}, {'fix_treshold': 15.25, 'max_num_fixes': 2}, {'fix_treshold': 15.25, 'max_num_fixes': 3}, {'fix_treshold': 15.25, 'max_num_fixes': 4}, {'fix_treshold': 15.25, 'max_num_fixes': 5}, {'fix_treshold': 20.0, 'max_num_fixes': 1}, {'fix_treshold': 20.0, 'max_num_fixes': 2}, {'fix_treshold': 20.0, 'max_num

In [147]:
hypotheses = [[] for each_ in range(len(parameters_grid_list))]

In [134]:
hypotheses

[['\ufeffесть у вас оформленный и подписанный мною заказ',
  'вот в инете откапал такую интересную статейку предлагаю вашему вниманию',
  'и на всю жизнь запомню свое первое купание в зимнем ледяном енисее',
  'думаем что не ошибемся если скажем что выставка лучшие фотографии россии 2012 станет одним из самых значимых событий в культурной жизни перми и ее жителей',
  'судьбе человека может складываться очень разнообразно в жизни много прекрасных светлых радостных моментов',
  'а я думаю вот если бы хозяин этой лодки тебе ее подарил и ты бы собрал знакомых и устроил на этой лодке большое катания с размахом',
  'например парадный портрет никола ii при орденах и регалиях освященный как икона и снабженный 5-рублевой монетой и роскошным текстом внизу',
  'двубортное кашемировое пальто песочного цвета классического фасона',
  'поговорил с директором и он мне обещал позвонить вечером и сказать берет он меня на работу',
  'схездил потом в ркб оказалось что на нем и царапины купил мази и капли'

In [148]:

for sent_idx, each_data in enumerate(results_data):
    for estimator_idx, each_estimator_param in enumerate(parameters_grid_list):
        sentence_hypothesis = fixes_maker(each_data, remove_s=True, **each_estimator_param)
        hypotheses[estimator_idx].append(sentence_hypothesis)
    

In [149]:
# evaluate each estimator:
filtered_erroneous_lines = [each_data['input_sentence'] for each_data in results_data]
filtered_golden_lines = [each_data['golden_sentence'] for each_data in results_data]

for estimator_idx, each_estimator_param in enumerate(parameters_grid_list):
    results = evaluate_spelling_corrector(filtered_erroneous_lines, 
                                          filtered_golden_lines, 
                                          hypotheses[estimator_idx])
    print(estimator_idx)
    print(each_estimator_param)
    print("f1:")
    print(results['f_measure'])
    print("precision:")
    print(results['precision'])
    print("_____")
# pprint.pprint(results)

Precision=25.89 Recall=25.73 FMeasure=25.81
246 950 956
0
{'fix_treshold': 1.0, 'max_num_fixes': 1}
f1:
0.25813221406086045
precision:
0.25894736842105265
_____
Precision=21.43 Recall=26.36 FMeasure=23.64
252 1176 956
1
{'fix_treshold': 1.0, 'max_num_fixes': 2}
f1:
0.23639774859287055
precision:
0.21428571428571427
_____
Precision=20.02 Recall=26.67 FMeasure=22.87
255 1274 956
2
{'fix_treshold': 1.0, 'max_num_fixes': 3}
f1:
0.22869955156950672
precision:
0.2001569858712716
_____
Precision=19.44 Recall=26.67 FMeasure=22.49
255 1312 956
3
{'fix_treshold': 1.0, 'max_num_fixes': 4}
f1:
0.22486772486772486
precision:
0.19435975609756098
_____
Precision=19.22 Recall=26.67 FMeasure=22.34
255 1327 956
4
{'fix_treshold': 1.0, 'max_num_fixes': 5}
f1:
0.2233902759526938
precision:
0.19216277317256972
_____
Precision=53.15 Recall=24.69 FMeasure=33.71
236 444 956
5
{'fix_treshold': 5.75, 'max_num_fixes': 1}
f1:
0.3371428571428572
precision:
0.5315315315315315
_____
Precision=51.72 Recall=25.21 FMea

In [142]:
results.keys()

dict_keys(['precision', 'recall', 'f_measure', 'answer_corrections', 'etalon_corrections'])

# Analyze advantages of LM for Golden Word and for hypothesis


In [22]:
# loop over sentences that has the same number of tokens as in correct answer
hypotheses = []
filtered_erroneous_lines = []
filtered_golden_lines = []
start_dt = dt.datetime.now()
for idx, each_error_line in enumerate(erroneous_lines):
#     if idx<10:continue
    err_toks = each_error_line.split()
    gold_toks = golden_lines[idx].split()
    if len(gold_toks) == len(err_toks):
        
        print("Sentence with the same number of toks:\n %s" % each_error_line)
        print("Golden answer:\n %s" % golden_lines[idx])
#         input_sentence = "обломно шо не сдал горбачева но хочу сдать последний экзам на 5 тогда буит возможно хоть ченить выловить на горбачеве"
#         golden_sentence ="обломно что не сдал горбачева но хочу сдать последний экзамен на 5 тогда будет возможно хоть что-нибудь выловить на горбачеве"
        res = elmo1_substitutor_spelling_corrector_dict_out(each_error_line)
#         res
#         print("input_sentence:")
#         print(input_sentence)
#         print("golden_sentence:")
#         print(golden_sentence)
#         print("hypothesis_sentence:\n %s" % res['hypothesis_sentence'])
        print("Hypothesis answer:\n %s" % res['hypothesis_sentence'])

        results = answer_analysis_fn(each_error_line, res['hypothesis_sentence'], golden_lines[idx], res)
#         results
#         result = selmosc([each_error_line])[0]
        
        filtered_erroneous_lines.append(each_error_line)
        filtered_golden_lines.append(golden_lines[idx])
        hypotheses.append(res['hypothesis_sentence'])
        
#         
        print("________________________________________")
#     if idx>18:
#         break
fin_dt = dt.datetime.now()
print("Total time for inference:")
print(fin_dt-start_dt)
results = evaluate_spelling_corrector(filtered_erroneous_lines, 
                                      filtered_golden_lines, 
                                      hypotheses)
print(results['precision'])
print(results['recall'])
print(results['f_measure'])

Sentence with the same number of toks:
 ﻿есть у вас оформленый и подписаный мною заказ
Golden answer:
 ﻿есть у вас оформленный и подписанный мною заказ
Hypothesis answer:
 ﻿есть у вас оформленый и подписанный мною заказ
Tokens differ in (input) оформленый -> оформленный (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): оформленый
elmo_word_substitution_advantage for substitution: оформленый->оформленный
12.21711594624432
UNK: ﻿есть| 
UNK: ﻿есть| UNK: оформленый| UNK: подписаный| 
log_i_probas[:, tok_idx]
[-16.93058156 -18.16913737]
log_g_probas[:, tok_idx]
[-16.17253849  -6.71006449]
golden_word_substitution_advantage  оформленый->оформленный:
12.217115946244341
____
Tokens differ in (input) подписаный -> подписанный (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): подписанный
elmo_word_substitution_advantage for substitution: подписаный->подписанный
22.162680332152007
UNK: ﻿есть| 
UNK: ﻿есть| UNK: оформленый| UNK: подписаный| 
log_i_probas[:, tok_idx]
[-15

Hypothesis answer:
 но даже когда мы приблизились к нижнему уровню замка и поверить не могла что он такой огромный как показывалось на карте
________________________________________
Sentence with the same number of toks:
 давно стоит понять что в этой жизни никто не зделает так как лутче тебе
Golden answer:
 давно стоит понять что в этой жизни никто не сделает так как лучше тебе
Hypothesis answer:
 давно стоит понять что в этой жизни никто не делает так как лутче тебе
Tokens differ in (input) зделает -> сделает (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): делает
elmo_word_substitution_advantage for substitution: зделает->делает
22.860682119348724

UNK: зделает| UNK: лутче| 
log_i_probas[:, tok_idx]
[-19.55872733 -18.74889021]
log_g_probas[:, tok_idx]
[ -6.10013221 -13.37595129]
golden_word_substitution_advantage  зделает->сделает:
18.831534034081272
____
Tokens differ in (input) лутче -> лучше (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): лутче
elmo

Hypothesis answer:
 на второй день своего пребывания в общаге я заметил теннисный стол в общей комнате в доме напротив
Tokens differ in (input) прибывания -> пребывания (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): пребывания
elmo_word_substitution_advantage for substitution: прибывания->пребывания
15.869327532939167


log_i_probas[:, tok_idx]
[ -8.60031201 -11.99157839]
log_g_probas[:, tok_idx]
[-0.90091779 -3.82164507]
golden_word_substitution_advantage  прибывания->пребывания:
15.86932753293916
____
________________________________________
Sentence with the same number of toks:
 последние пять тысяч лет человеческая нога туда не ступала даже у восьмого департамента что-то не сложилось
Golden answer:
 последние пять тысяч лет человеческая нога туда не ступала даже у восьмого департамента что-то не сложилось
Hypothesis answer:
 последние пять тысяч лет человеческая нога куда не ступала даже у восьмого департамента что-то не сложилось
_________________________________

Hypothesis answer:
 в середине десятилетия увлечение вампирами изжевало себя
Tokens differ in (input) изжевало -> изживало (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): изжевало
elmo_word_substitution_advantage for substitution: изжевало->None
-inf
UNK: изживало| 
UNK: изжевало| 
log_i_probas[:, tok_idx]
[-19.1098897  -18.70677979]
log_g_probas[:, tok_idx]
[-19.1098897  -18.70677979]
golden_word_substitution_advantage  изжевало->изживало:
0.0
____
________________________________________
Sentence with the same number of toks:
 жека довел торги до 1000 но охранник не приклонился хотя оч хотел
Golden answer:
 жека довел торги до 1000 но охранник не преклонился хотя очень хотел
Hypothesis answer:
 жека довел торги до 1000 но охранник не приклонился хотя он хотел
Tokens differ in (input) приклонился -> преклонился (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): приклонился
elmo_word_substitution_advantage for substitution: приклонился->прислонился
5.741097

Hypothesis answer:
 сегодня китай закупает более двух третей произведенной в судне нефти
________________________________________
Sentence with the same number of toks:
 многие ультра-националисты и другие люди положительно бы отнеслись к подобному решению вопроса
Golden answer:
 многие ультра-националисты и другие люди положительно бы отнеслись к подобному решению вопроса
Hypothesis answer:
 многие ультранационалисты и другие люди положительно бы отнеслись к подобному решению вопроса
________________________________________
Sentence with the same number of toks:
 найдены также остатки мыла которое викинги делали самостоятельно
Golden answer:
 найдены также остатки мыла которое викинги делали самостоятельно
Hypothesis answer:
 найдены также остатки мыла которые викинги делали самостоятельно
________________________________________
Sentence with the same number of toks:
 география его выступлений достегает индии англии венгрии португалии голландии финляндии
Golden answer:
 география его

...

Hypothesis answer:
 тут интересно довольно-таки отличается от того что я ожидал
________________________________________
Sentence with the same number of toks:
 или митинговать отправятся а это лишняя головная боль
Golden answer:
 или митинговать отправятся а это лишняя головная боль
Hypothesis answer:
 или митинговать отправятся и это лишняя головная боль
________________________________________
Sentence with the same number of toks:
 а где ето сделать ясно что лучшего варианта чем какое-либо место древлей боевой славы не найти
Golden answer:
 а где это сделать ясно что лучшего варианта чем какое-либо место древней боевой славы не найти
Hypothesis answer:
 а где это сделать ясно что лучшего варианта чем какое-либо место древлей боевой славы не найти
Tokens differ in (input) ето -> это (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): это
elmo_word_substitution_advantage for substitution: ето->это
23.809152589503924

UNK: древлей| 
log_i_probas[:, tok_idx]
[-15.88474291 -

Hypothesis answer:
 нет ни одного места для того чтобы тупо присесть подождать посадки куда народу везде
________________________________________
Sentence with the same number of toks:
 любимая женщина посетовав на то что зверь скушный и худой вымела из клетки перловку и положила вместо нее три разных кусочка сыра курагу чернослив дольку яблока сечечки орешки грецкие и арахис
Golden answer:
 любимая женщина посетовав на то что зверь скучный и худой вымела из клетки перловку и положила вместо нее три разных кусочка сыра курагу чернослив дольку яблока семечки орешки грецкие и арахис
Hypothesis answer:
 любимая женщина посетовав на то что зверь скушный и худой вымела из клетки перловку и положила вместо нее три разных кусочка сыра курагу чернослив дольку яблока семечки орешки грецкие и арахис
Tokens differ in (input) скушный -> скучный (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): скушный
elmo_word_substitution_advantage for substitution: скушный->скудный
11.998270126039

Hypothesis answer:
 знания культуры никогда не бывают изолированными всегда подвергаются взаимному влиянию
________________________________________
Sentence with the same number of toks:
 в то время как именно обращение к ней избавляет от приглушения чувств повседневностью
Golden answer:
 в то время как именно обращение к ней избавляет от приглушения чувств повседневностью
Hypothesis answer:
 в то время как именно обращение к ней избавляет от приглашения чувств повседневностью
________________________________________
Sentence with the same number of toks:
 традиционно натуральный подбор видется чем-то совсем однозначным
Golden answer:
 традиционно натуральный подбор видится чем-то совсем однозначным
Hypothesis answer:
 традиционно натуральный подбор ведется чем-то совсем однозначным
Tokens differ in (input) видется -> видится (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): ведется
elmo_word_substitution_advantage for substitution: видется->ведется
15.834135664114854

UN

Hypothesis answer:
 я загорел за эти дни и проходя через бар нередко ловил на себе заинтересованные взгляды женской половины отдыхающих
Tokens differ in (input) довил -> ловил (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): ловил
elmo_word_substitution_advantage for substitution: довил->ловил
21.41345652318296

UNK: довил| 
log_i_probas[:, tok_idx]
[-18.53729202 -18.03220215]
log_g_probas[:, tok_idx]
[-8.78653498 -6.36950267]
golden_word_substitution_advantage  довил->ловил:
21.41345652318294
____
________________________________________
Sentence with the same number of toks:
 по пусти на плошадку оказалось что историчные ботиночки по снегу очень даже ничего
Golden answer:
 по пути на площадку оказалось что историчные ботиночки по снегу очень даже ничего
Hypothesis answer:
 по пути на плошадку оказалось что историчные ботиночки по снегу очень даже ничего
Tokens differ in (input) пусти -> пути (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): пути
elmo_word

Hypothesis answer:
 человек который согласно прилагаемой биографии более всего
________________________________________
Sentence with the same number of toks:
 надеюсь что будет вкууусно
Golden answer:
 надеюсь что будет вкусно
Hypothesis answer:
 надеюсь это будет вкууусно
Tokens differ in (input) вкууусно -> вкусно (golden) 
Hypothesis (ELMO SC with 1 substitution in sentence): вкууусно
elmo_word_substitution_advantage for substitution: вкууусно->None
-inf

UNK: вкууусно| 
log_i_probas[:, tok_idx]
[-20.28374628 -22.58180983]
log_g_probas[:, tok_idx]
[ -8.57395621 -22.48953154]
golden_word_substitution_advantage  вкууусно->вкусно:
11.802068363852285
____
________________________________________
Sentence with the same number of toks:
 затем ручейками капли начинаю стекать по лбу дальше котясь по щекам слетая с кончика носа
Golden answer:
 затем ручейками капли начинают стекать по лбу дальше катясь по щекам слетая с кончика носа
Hypothesis answer:
 затем ручейками капли начинаю стекать 

# measure time advantage for batching with elmo

In [ ]:
# if you use 2 or 3 setences in a batch then consequent run is more effective!
# but if you take >=10 sentences, then batching is advantageous
sentences = ["дама рыла ламу", 
             "на реконструкции дворца понятно что обозлились слишком хороше для киева сделал",
            "ты сам себе создаешь проблемы пойми что мир не будет приклонятся перед тобой и притиратся к твоим взглядам",
            "схездил птом в ркб оказалось что на нем 3 царапины купил мази и капли",
             "схездил потом в ркб оказалось что на нем 3 царапины купил мази и капли",
             "схездил потом в ркб оказалось что на нем 3 царапины купил мази и капли",
             "но даже когда мы приблизились к нижнему уровню замка я поверить не могла что он такой огромный как показывалось на карте",
            "давно стоит понять что в этой жизни никто не зделает так как лутче тебе",
             "давно стоит понять что в этой жизни никто не делает так как лутче тебе."
            ]
tok_sents_wrapped = elmo.tokenize_sentence_batch(sentences)

start_dt = dt.datetime.now()
for idx, each_sent in enumerate(sentences):
    elmo.elmo_lm(tok_sents_wrapped[idx])
fin_dt = dt.datetime.now()
print("Total time for inference iteratively:")
print(fin_dt-start_dt)

############################

start_dt2 = dt.datetime.now()
elmo.elmo_lm(tok_sents_wrapped)
fin_dt2 = dt.datetime.now()
print("Total time for inference batchy:")
print(fin_dt2-start_dt2)
